In [1]:
from brainmri.nn import predict_ga, Net
import pickle

mri_images = pickle.load(open('mri_images.pkl', 'rb'))

Loading Images


In [2]:
len(mri_images)

229

In [3]:
mri_images[0].filename

'fm0216_t2_recon_2_mask_brain_tissue.nii'

In [14]:
losses = []
for mri_image in mri_images:
    true_ga = mri_image.ga
    if true_ga is None or true_ga < 10:
        continue
    pred_ga = predict_ga(mri_image)
    loss = abs(pred_ga - true_ga)
    losses.append(loss)

In [15]:
import numpy as np
print(f"Off by {round(np.mean(losses), 2)} ± {round(np.std(losses), 2)} weeks")

Off by 1.5 ± 1.64 weeks


In [16]:
from brainmri.core import get_total_volume_in_ml, get_head_circumference
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split

In [17]:
from brainmri.nn import predict_ga_reg
import numpy as np

losses = []
for mri_image in mri_images:
    ga = mri_image.ga
    if ga is None or ga < 10:
        continue
    ga_pred = predict_ga_reg(mri_image)
    ga_pred_conv = predict_ga(mri_image)
    ga_avg = (ga_pred + ga_pred_conv) / 2
    loss = abs(ga - ga_avg)
    losses.append(loss)

print(f"Off by {round(np.mean(losses), 2)} ± {round(np.std(losses), 2)} weeks")

Off by 1.49 ± 1.55 weeks


In [18]:
X = []
y = []
for mri_image in mri_images:
    ga = mri_image.ga
    if ga is None or ga < 10:
        continue
    vol = get_total_volume_in_ml(mri_image)
    hc = get_head_circumference(mri_image)
    X.append([vol, hc])
    y.append(ga)

In [19]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

reg = LinearRegression().fit(X_train, y_train)
print(f"R^2: {reg.score(X_test, y_test)}")

R^2: 0.8209603896071176


In [20]:
pickle.dump(reg, open("reg.pkl", "wb"))

In [26]:
import numpy as np
import plotly.graph_objs as go

X_test_np = np.array(X_test)

z_pred = reg.predict(X_test_np)

x_surf, y_surf = np.meshgrid(np.linspace(X_test_np[:,0].min(), X_test_np[:,0].max(), 100), 
                             np.linspace(X_test_np[:,1].min(), X_test_np[:,1].max(), 100))
z_surf = reg.intercept_ + reg.coef_[0] * x_surf + reg.coef_[1] * y_surf

scatter_real = go.Scatter3d(
    x=X_test_np[:,0],
    y=X_test_np[:,1],
    z=y_test,
    mode='markers',
    marker=dict(size=3, color='red')
)

scatter_pred = go.Scatter3d(
    x=X_test_np[:,0],
    y=X_test_np[:,1],
    z=z_pred.ravel(),
    mode='markers',
    marker=dict(size=3, color='blue')
)

surface = go.Surface(
    x=x_surf,
    y=y_surf,
    z=z_surf,
    colorscale=[[0, 'green'], [1, 'green']],
    opacity=0.5,
    showscale=False,
    showlegend=True
)

data = [scatter_real, scatter_pred, surface]

layout = go.Layout(
    scene=dict(
        xaxis_title='Volume (ml)',
        yaxis_title='Head Circumference (cm)',
        zaxis_title='Gestational Age (weeks)'
    ),
    height=800
)

fig = go.Figure(data=data, layout=layout)
fig.show()

In [27]:
import plotly.offline as pyo

pyo.plot(fig, filename='reg3d.html', auto_open=False)

'reg3d.html'

In [39]:
import plotly.graph_objs as go

gas = []
for mri_image in mri_images:
    ga = mri_image.ga
    if ga is None or ga < 10:
        continue
    gas.append(ga)

fig = go.Figure()
fig.add_trace(go.Histogram(x=gas, histnorm='', nbinsx=50))
fig.update_layout(
    title_text='Distribution of Gestational Ages',
    xaxis_title_text='Gestational Age (weeks)',
    yaxis_title_text='Probability',
    bargap=0.2,
    bargroupgap=0.1,
)
fig.update_xaxes(range=[0, 40])
fig.show()

In [54]:
import plotly.graph_objs as go
import numpy as np
import plotly.io as pio
import matplotlib.cm as cm
import matplotlib.pyplot as plt


slices = mri_images[0].slices_z
stack = []

for i, slice in enumerate(slices[50:]):
    x, y = np.where(slice > 0) # retain this to limit to non-zero elements
    z = [i]*len(x)
    intensity = slice[x, y] 
    for xi, yi, zi, intensity_i in zip(x, y, z, intensity):
        stack.append([xi, yi, zi, intensity_i])

stack = np.array(stack)

# Identify unique intensities and corresponding indices
unique_intensities, inverse = np.unique(stack[:, 3], return_inverse=True)
cmap = plt.cm.get_cmap('jet', len(unique_intensities))
colors = cmap(inverse, bytes=True)

fig = go.Figure(data=go.Scatter3d(
    x = stack[:, 0],
    y = stack[:, 1],
    z = stack[:, 2],
    mode = 'markers',
    marker=dict(
        size=5,
        color=['rgba'+str(tuple(val)) for val in colors],
        opacity=0.01,
    )
))
fig.show()
pio.show()


/var/folders/wz/450ykx4x3w55ggphrbl9w4540000gn/T/ipykernel_4681/2042940446.py:25: MatplotlibDeprecationWarning:

The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.



In [47]:
import plotly
import plotly.express as px
import numpy as np
import matplotlib.pyplot as plt

fig = px.imshow(np.array(mri_images[0].slices_z), animation_frame=0, binary_string=True)
fig.update_xaxes(showticklabels=False)
fig.update_yaxes(showticklabels=False)
fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    coloraxis_showscale=False
)
# Drop animation buttons
fig['layout'].pop('updatemenus')
plotly.io.show(fig)

plt.show()

In [46]:
# import plotly.graph_objects as go
# import numpy as np

# slices = mri_images[0].slices_z

# # Stack the slices into a 3D volume
# volume = np.stack(slices)

# # Visualize the 3D Volume
# fig = go.Figure(data=go.Isosurface(
#     x=volume[0].flatten(),
#     y=volume[1].flatten(),
#     z=volume[2].flatten(),
#     value=volume.flatten(),
#     isomin=np.min(volume),
#     isomax=np.max(volume),
#     surface=dict(count=5, fill=0.7, pattern='odd'),
#     caps=dict(x_show=False, y_show=False, z_show=False),
#     colorscale='Blues',
#     showscale=False))
# fig.show()


In [44]:
mri_images[0].slices_z[55]

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [27]:
pio.write_html(fig, 'mri_slices2.html')